# RelationalAI Native App Setup Guide

> :warning: Note that the `ACCOUNTADMIN` role is used in this guide. This role is needed for Step 1 and for creating the network rule in Step 4. To manage roles specific the RelationalAI Native App, see Appendix 2 at the bottom of this notebook.


In [ ]:
USE ROLE ACCOUNTADMIN;

## Step 1 - Activate the RAI Native App

The *Grant* button under *Data Products > Apps > RelationalAI* in Snowsight runs the following SQL command to grant the necessary permissions to the app. If you haven't clicked that button yet, you can run the code here instead. It doesn't hurt to run it again if you're not sure.


In [ ]:
GRANT
      EXECUTE TASK,
      EXECUTE MANAGED TASK,
      CREATE COMPUTE POOL,
      CREATE WAREHOUSE
ON ACCOUNT TO APPLICATION RELATIONALAI;

Now execute the following three cells to create the RAI service (this usually takes between 5 and 15 minutes):


In [ ]:
import sys
import time
import json
import itertools

session = get_active_session()

def poll(f):

    last_message = ""
    dots = itertools.cycle(["⠧", "⠏", "⠛", "⠹", "⠼", "⠶"])

    def status(message):
        spaces = " " * (len("⠿ " + last_message) - len(message))
        sys.stdout.write("\r" + message + spaces)
        sys.stdout.flush()

    for ctr in itertools.count():
        if ctr % 10 == 0:
            result = f()
            if isinstance(result, str):
                message = next(dots) + " " + result
                status(message)
                last_message = result
            if result is True:
                status("⠿ Done!")
                return
        else:
            message = next(dots) + " " + last_message
            status(message)
        time.sleep(0.5)

In [ ]:
def activate():
    try:
        session.sql("CALL RELATIONALAI.APP.ACTIVATE();").collect()
        return True
    except Exception as e:
        if "Unknown user-defined function" in str(e):
            return "Waiting for app installation to complete..."
        else:
            raise e

poll(activate)

In [ ]:
def check():
    result = session.sql("CALL RELATIONALAI.APP.SERVICE_STATUS();").collect()
    status = json.loads(result[0]["SERVICE_STATUS"])[0]["message"]
    if status.startswith("UNKNOWN"):
        status = "Working"
    if status.startswith("Readiness probe"):
        status = "Almost done"
    if status == "Running":
        return True
    else:
        return status + "..."

poll(check)

> :warning: Note: Please review the [documentation on upgrades](https://relational.ai/docs/manage/upgrades) for details about the weekly automatic upgrade schedule.



## Step 2 - Setting up Change Data Capture

Streams share Snowflake data with the RAI Native App using change data capture (CDC) to capture source table and view changes once every minute.

To enable CDC, run the following command:


In [ ]:
CALL RELATIONALAI.APP.RESUME_CDC();

## Step 3 - Creating user roles

The RAI Native App comes with a set of Snowflake application roles for managing access to the app. Application roles can't be granted to users directly, and must be granted to Snowflake database roles instead.

The following SQL creates two database roles: `rai_admin` and `rai_developer`. The `rai_admin` role is for full admin access to the RAI Native App, while the `rai_developer` role is for developers who need access to the RAI Python API:


In [ ]:
-- Create a rai_admin role for full admin access to the RAI Native App.
CREATE ROLE rai_admin;
-- Link the app's `all_admin` role to the created role.
GRANT APPLICATION ROLE relationalai.all_admin TO ROLE rai_admin;

-- Create a role for developers who need access to the RAI Python API.
CREATE ROLE rai_developer;
-- Link the app's `rai_user` role to the created role.
GRANT APPLICATION ROLE relationalai.rai_user TO ROLE rai_developer;

Users granted the `rai_developer` role can:

- Use the RAI Native App.
- Create, use, and delete RAI engines.
- Create, manage, and delete data streams.
- Enable and disable the CDC service.

You can grant the `rai_developer` role to users in your Snowflake account using the `GRANT ROLE rai_developer TO USER &quot;username&quot;;` command. For example, to grant the `rai_developer` role to yourself, run the following cell:


In [ ]:
# optional: grant the rai_developer role to yourself
session = get_active_session()
current_user = session.sql("SELECT CURRENT_USER() AS USERNAME;").collect()[0]["USERNAME"]

session.sql(f'GRANT ROLE rai_developer TO USER "{current_user}"').collect()

Our [Simple Start notebook](https://relational.ai/notebooks/simple-start-snowflake.ipynb) uses a table called `RAI_DEMO.SIMPLE_START.CONNECTIONS`. If you want to be able to run that notebook, either grant permissions to the `rai_developer` role or run the following SQL to create the table now. You can clean up this database when you're done with the demo notebook by running `DROP DATABASE RAI_DEMO CASCADE;`


In [ ]:
CREATE DATABASE IF NOT EXISTS RAI_DEMO;
CREATE SCHEMA IF NOT EXISTS RAI_DEMO.SIMPLE_START;

CREATE OR REPLACE TABLE RAI_DEMO.SIMPLE_START.CONNECTIONS (
    STATION_1 INT,
    STATION_2 INT
);

INSERT INTO RAI_DEMO.SIMPLE_START.CONNECTIONS (STATION_1, STATION_2) VALUES
(1, 2),
(1, 3),
(3, 4),
(1, 4),
(4, 5),
(5, 7),
(6, 7),
(6, 8),
(7, 8);

GRANT USAGE ON DATABASE RAI_DEMO TO ROLE rai_developer;
GRANT USAGE ON SCHEMA RAI_DEMO.SIMPLE_START TO ROLE rai_developer;
GRANT SELECT ON TABLE RAI_DEMO.SIMPLE_START.CONNECTIONS TO ROLE rai_developer;
ALTER TABLE RAI_DEMO.SIMPLE_START.CONNECTIONS SET CHANGE_TRACKING = TRUE;

-- optional: give rai_developer more extensive permissions in the RAI_DEMO database
-- this step is necessary for the user to be able to run all the demo notebooks
GRANT CREATE SCHEMA ON DATABASE RAI_DEMO TO ROLE rai_developer;
GRANT CREATE TABLE ON SCHEMA RAI_DEMO.SIMPLE_START TO ROLE rai_developer;
GRANT CREATE TABLE ON FUTURE SCHEMAS IN DATABASE RAI_DEMO TO ROLE rai_developer;
GRANT SELECT ON ALL TABLES IN SCHEMA RAI_DEMO.SIMPLE_START TO ROLE rai_developer;
GRANT SELECT ON FUTURE TABLES IN DATABASE RAI_DEMO TO ROLE rai_developer;

## Step 4 — Setting up Snowflake Notebooks

Snowflake offers two options when you create a new Snowflake Notebook: *Run on Warehouse* and *Run on Container*. We recommend using container notebooks because they support the use of `pip` to install the latest version of the RelationalAI Python library.

For more information on using RelationalAI in Snowflake Notebooks, see [Using RAI in a Cloud Notebook](https://relational.ai/docs/get-started/cloud-notebook) in the RelationalAI documentation.

### Container Notebooks

Container notebooks do require a bit of additional setup because (1) they can't be executed with account administrator privileges, and (2) they require you to select a compute pool when creating a notebook.

The SQL code below sets up all the necessary resources and permissions to simplify the process of using Container notebooks:


In [ ]:
-- create a database to contain the notebooks
CREATE DATABASE rai_notebooks;

-- create a warehouse to select when creating a notebook
CREATE WAREHOUSE notebooks_wh;

-- create a compute pool to use when creating a notebook
CREATE COMPUTE POOL NOTEBOOK_CPU_XS
  MIN_NODES = 1
  MAX_NODES = 15
  INSTANCE_FAMILY = CPU_X64_XS
  AUTO_RESUME = true
  AUTO_SUSPEND_SECS = 1800
  COMMENT = "Pool for Snowflake Notebooks on Container Runtime";

-- grant the necessary permissions to the rai_developer role
GRANT USAGE ON DATABASE rai_notebooks TO ROLE rai_developer;
GRANT USAGE ON SCHEMA rai_notebooks.public TO ROLE rai_developer;
GRANT CREATE NOTEBOOK ON SCHEMA rai_notebooks.public TO ROLE rai_developer;
GRANT USAGE ON WAREHOUSE notebooks_wh TO ROLE rai_developer;
GRANT USAGE ON COMPUTE POOL NOTEBOOK_CPU_XS TO ROLE rai_developer;
GRANT CREATE SERVICE ON SCHEMA rai_notebooks.public TO ROLE rai_developer;

If you want to be able to install Python packages from PyPI in your notebooks, run the code below to set up an External Access Integration:

> If you don't want to enable a PyPI integration, you can skip this step. Notebook users can import the RelationalAI Python library by uploading a ZIP file instead.


In [ ]:
-- grant the necessary permissions to the rai_developer role
CREATE OR REPLACE NETWORK RULE pypi_network_rule
MODE = EGRESS
TYPE = HOST_PORT
VALUE_LIST = ('pypi.org', 'pypi.python.org', 'pythonhosted.org',  'files.pythonhosted.org');

CREATE OR REPLACE EXTERNAL ACCESS INTEGRATION pypi_access_integration
ALLOWED_NETWORK_RULES = (pypi_network_rule)
ENABLED = true;

GRANT USAGE ON INTEGRATION pypi_access_integration TO ROLE rai_developer;

### Warehouse Notebooks

The RelationalAI Python library requires an [External Access Integration](https://docs.snowflake.com/en/sql-reference/sql/create-external-access-integration) to work on notebooks that run on a warehouse. This integration allows the app to pass query results back to the notebook. Run the following code to set up the integration:


In [ ]:
session = get_active_session()

system_allowlist = session.sql("""
SELECT value:host AS URL
FROM TABLE(FLATTEN(input=>parse_json(SYSTEM$ALLOWLIST())))
WHERE value:type = 'STAGE'
""").collect()

if system_allowlist:
    urls = ", ".join(row.URL.replace('"', "'") for row in system_allowlist)
    egress_rule_commands = [
        f"""
        CREATE OR REPLACE NETWORK RULE S3_RAI_INTERNAL_BUCKET_EGRESS
        MODE = EGRESS
        TYPE = HOST_PORT
        VALUE_LIST = ({urls});
        """,
        """
        CREATE OR REPLACE EXTERNAL ACCESS INTEGRATION S3_RAI_INTERNAL_BUCKET_EGRESS_INTEGRATION
        ALLOWED_NETWORK_RULES = (S3_RAI_INTERNAL_BUCKET_EGRESS)
        ENABLED = true;
        """,
        """
        GRANT USAGE ON INTEGRATION S3_RAI_INTERNAL_BUCKET_EGRESS_INTEGRATION TO ROLE rai_developer;
        """
    ]

    for command in egress_rule_commands:
        session.sql(command).collect()

    print("Network rule set up successfully.")

## Congratulations! Your RelationalAI app is now ready to use.

# Next Steps

To get up and running with RelationalAI in Snowflake Notebooks, download the [Simple Start Snowflake Notebook](https://relational.ai/notebooks/simple-start-snowflake.ipynb), upload it to your Snowflake account (https://app.snowflake.com > + icon in left sidebar > Notebooks > Import .ipynb file), and follow the instructions in the notebook.

To use a local Python installation instead, download the [Simple Start Jupyter notebook](https://relational.ai/notebooks/simple-start.ipynb) and follow the [instructions for running the notebook](https://relational.ai/docs/develop/example-notebooks#instructions).

For a more detailed example and more information about the RelationalAI Python library, check out the [Getting Started guide](https://relational.ai/docs/get-started).

Links:

- Simple Start Notebook: https://relational.ai/notebooks/simple-start.ipynb
- Example Notebooks: https://relational.ai/docs/develop/example-notebooks
- Docs: https://relational.ai/docs

## APPENDIX 1 - Deactivate the RAI Native App

To reduce costs when you are not using the RAI Native App, suspend CDC, and delete all engines.

> :warning: Note that this task requires the `app_admin` application role.


In [ ]:
session = get_active_session()
# note: the use of `skip_appendix` in the Appendices makes the notebook's
# "Run All" action skip these cells
skip_appendix = True

# Deactivate the app
if not skip_appendix:
    session.sql("CALL RELATIONALAI.APP.DEACTIVATE();").collect()

# To re-activate the app:
# session.sql("CALL RELATIONALAI.APP.ACTIVATE();").collect()

## APPENDIX 2 - App Upgrades

Your RAI Native App is [automatically upgraded](https://relational.ai/docs/native_app/upgrades) every Monday at 10:00 UTC. During upgrades, the application cannot process RAI transactions.

If you prefer to schedule upgrades for a different day and time, use the [`schedule_upgrade()`](https://relational.ai/docs/reference/sql/schedule_upgrade) procedure:


In [ ]:
if not skip_appendix:
    # Schedule upgrades for Wednesdays at 15:00 UTC. Times are in 24-hour format.
    session.sql("CALL relationalai.app.schedule_upgrade('WEDNESDAY', '15:00');").collect()